# Explore here

In [4]:
import pandas as pd
import sqlite3
import json
from sklearn.model_selection import train_test_split
import pickle

#### Paso 1: Carga del conjunto de datos

In [5]:
pd.set_option('display.max_columns', None)
movies = pd.read_csv('/Users/julian/Desktop/vs code/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/data/raw/tmdb_5000_movies.csv', sep = ',')
credits = pd.read_csv('/Users/julian/Desktop/vs code/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/data/raw/tmdb_5000_credits.csv', sep = ',')
movies.head()

budget                                             genres  \
0  237000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
1  300000000  [{"id": 12, "name": "Adventure"}, {"id": 14, "...   
2  245000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
3  250000000  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4  260000000  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   

                                       homepage      id  \
0                   http://www.avatarmovie.com/   19995   
1  http://disney.go.com/disneypictures/pirates/     285   
2   http://www.sonypictures.com/movies/spectre/  206647   
3            http://www.thedarkknightrises.com/   49026   
4          http://movies.disney.com/john-carter   49529   

                                            keywords original_language  \
0  [{"id": 1463, "name": "culture clash"}, {"id":...                en   
1  [{"id": 270, "name": "ocean"}, {"id": 726, "na...                en   
2  [{"id": 470, "name": "spy"}, {"id": 818, "name...                en   
3  [{"id": 849, "name": "dc comics"}, {"id": 853,...                en   
4  [{"id": 818, "name": "based on novel"}, {"id":...                en   

                             original_title  \
0                                    Avatar   
1  Pirates of the Caribbean: At World's End   
2                                   Spectre   
3                     The Dark Knight Rises   
4                               John Carter   

                                            overview  popularity  \
0  In the 22nd century, a paraplegic Marine is di...  150.437577   
1  Captain Barbossa, long believed to be dead, ha...  139.082615   
2  A cryptic message from Bond’s past sends him o...  107.376788   
3  Following the death of District Attorney Harve...  112.312950   
4  John Carter is a war-weary, former military ca...   43.926995   

                                production_companies  \
0  [{"name": "Ingenious Film Partners", "id": 289...   
1  [{"name": "Walt Disney Pictures", "id": 2}, {"...   
2  [{"name": "Columbia Pictures", "id": 5}, {"nam...   
3  [{"name": "Legendary Pictures", "id": 923}, {"...   
4        [{"name": "Walt Disney Pictures", "id": 2}]   

                                production_countries release_date     revenue  \
0  [{"iso_3166_1": "US", "name": "United States o...   2009-12-10  2787965087   
1  [{"iso_3166_1": "US", "name": "United States o...   2007-05-19   961000000   
2  [{"iso_3166_1": "GB", "name": "United Kingdom"...   2015-10-26   880674609   
3  [{"iso_3166_1": "US", "name": "United States o...   2012-07-16  1084939099   
4  [{"iso_3166_1": "US", "name": "United States o...   2012-03-07   284139100   

   runtime                                   spoken_languages    status  \
0    162.0  [{"iso_639_1": "en", "name": "English"}, {"iso...  Released   
1    169.0           [{"iso_639_1": "en", "name": "English"}]  Released   
2    148.0  [{"iso_639_1": "fr", "name": "Fran\u00e7ais"},...  Released   
3    165.0           [{"iso_639_1": "en", "name": "English"}]  Released   
4    132.0           [{"iso_639_1": "en", "name": "English"}]  Released   

                                          tagline  \
0                     Enter the World of Pandora.   
1  At the end of the world, the adventure begins.   
2                           A Plan No One Escapes   
3                                 The Legend Ends   
4            Lost in our world, found in another.   

                                      title  vote_average  vote_count  
0                                    Avatar           7.2       11800  
1  Pirates of the Caribbean: At World's End           6.9        4500  
2                                   Spectre           6.3        4466  
3                     The Dark Knight Rises           7.6        9106  
4                               John Carter           6.1        2124

#### Paso 2: Creación de una base de datos

In [ ]:
#lo hago con with para asegurarme de que se cierre la concección y no se bloquee. 
with sqlite3.connect('DB_movies') as con: # Creo, doy nombre y me conecto a la base de datos sqlite.
    movies.to_sql('Movies_table', con, if_exists='replace', index=False)  # Inserto el dataframe en sql y lo combierto en una tabala de sql.
    credits.to_sql('Credits_table', con, if_exists='replace', index=False)  # Inserto el dataframe en sql y lo combierto en una tabala de sql.

In [7]:
# Muestro los resultados para verificar que he insertado bien los datos en la base de datos sql.
with sqlite3.connect('DB_movies') as con:
    
    cursor = con.cursor() # Creo el cursor para ejecutar la consulta.
    
    cursor.execute('SELECT * FROM Movies_table') # Ejecuto la consulta SELECT para obtener todos los datos de la tabla.
     
    data_rows = cursor.fetchall() # Obtener todos los resultados.
    
    for row in data_rows: # Mostrar los resultados.
        print(row)

(237000000, '[{"id": 28, "name": "Action"}, {"id": 12, "name": "Adventure"}, {"id": 14, "name": "Fantasy"}, {"id": 878, "name": "Science Fiction"}]', 'http://www.avatarmovie.com/', 19995, '[{"id": 1463, "name": "culture clash"}, {"id": 2964, "name": "future"}, {"id": 3386, "name": "space war"}, {"id": 3388, "name": "space colony"}, {"id": 3679, "name": "society"}, {"id": 3801, "name": "space travel"}, {"id": 9685, "name": "futuristic"}, {"id": 9840, "name": "romance"}, {"id": 9882, "name": "space"}, {"id": 9951, "name": "alien"}, {"id": 10148, "name": "tribe"}, {"id": 10158, "name": "alien planet"}, {"id": 10987, "name": "cgi"}, {"id": 11399, "name": "marine"}, {"id": 13065, "name": "soldier"}, {"id": 14643, "name": "battle"}, {"id": 14720, "name": "love affair"}, {"id": 165431, "name": "anti war"}, {"id": 193554, "name": "power relations"}, {"id": 206690, "name": "mind and soul"}, {"id": 209714, "name": "3d"}]', 'en', 'Avatar', 'In the 22nd century, a paraplegic Marine is dispatched t

In [ ]:
# Creo una nueva tabla de sql en la que uno las dos tablas anteriores para crear una nueva con INNER JOIN. 

with sqlite3.connect('DB_movies') as con:

    cursor = con.cursor()

    query = '''
    CREATE TABLE IF NOT EXISTS Movies_Credits AS
    SELECT *
    FROM Movies_table
    INNER JOIN Credits_table
    ON Movies_table.original_title = Credits_table.title
    '''
    
    cursor.execute(query)

# Confirmar que la tabla fue creada (opcional)
    cursor.execute("SELECT name FROM sqlite_master WHERE type='table';")
    print(cursor.fetchall())  # Esto imprimirá todas las tablas en la base de datos

[('Movies_Credits',), ('Movies_table',), ('Credits_table',)]


In [ ]:
# Hago una consulta en la que escojo las columnas de la tabla creada anteriormente que quiero y la extraigo como un nuevo dataframe para trabajar con el. 

with sqlite3.connect('DB_movies') as con:

    cursor = con.cursor()

    query = '''
            SELECT "movie_id", "title:1", "overview", "genres", "keywords", "cast", "crew" FROM Movies_Credits
            '''
    
    cursor.execute(query)

    data = pd.read_sql(query, con)


In [10]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  In the 22nd century, a paraplegic Marine is di...   
1  Captain Barbossa, long believed to be dead, ha...   
2  A cryptic message from Bond’s past sends him o...   
3  Following the death of District Attorney Harve...   
4  John Carter is a war-weary, former military ca...   

                                              genres  \
0  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
1  [{"id": 12, "name": "Adventure"}, {"id": 14, "...   
2  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   
3  [{"id": 28, "name": "Action"}, {"id": 80, "nam...   
4  [{"id": 28, "name": "Action"}, {"id": 12, "nam...   

                                            keywords  \
0  [{"id": 1463, "name": "culture clash"}, {"id":...   
1  [{"id": 270, "name": "ocean"}, {"id": 726, "na...   
2  [{"id": 470, "name": "spy"}, {"id": 818, "name...   
3  [{"id": 849, "name": "dc comics"}, {"id": 853,...   
4  [{"id": 818, "name": "based on novel"}, {"id":...   

                                                cast  \
0  [{"cast_id": 242, "character": "Jake Sully", "...   
1  [{"cast_id": 4, "character": "Captain Jack Spa...   
2  [{"cast_id": 1, "character": "James Bond", "cr...   
3  [{"cast_id": 2, "character": "Bruce Wayne / Ba...   
4  [{"cast_id": 5, "character": "John Carter", "c...   

                                                crew  
0  [{"credit_id": "52fe48009251416c750aca23", "de...  
1  [{"credit_id": "52fe4232c3a36847f800b579", "de...  
2  [{"credit_id": "54805967c3a36829b5002c41", "de...  
3  [{"credit_id": "52fe4781c3a36847f81398c3", "de...  
4  [{"credit_id": "52fe479ac3a36847f813eaa3", "de...

#### Paso 3: Transforma los datos

In [ ]:
# Transformo los datos de las columnas que vienen en formato json a un diccionario de pandas aplicando json.loads.

data['genres'] = data['genres'].apply(json.loads)
data['keywords'] = data['keywords'].apply(json.loads)
data['cast'] = data['cast'].apply(json.loads)
data['crew'] = data['crew'].apply(json.loads)

In [ ]:
# Con esta funcion accedo a el atributo name del diccionario y los meto en una lista, para luego aplicarle la funcion a el valor de celda y cambiar el diccionario por una lista con los nombres.  

def get_names(x):

    list_name = []  # Creamos una lista vacía para almacenar los nombres
    for i in x:  # Iteramos sobre cada elemento en la lista x
        if "name" in i:  # Verificamos que el diccionario tiene la clave "name"
            list_name.append(i["name"])  # Añadimos el nombre a la lista
    return list_name  # Retornamos la lista con los nombres

# Aplicamos la función a la columna 'genres' del dataframe
data["genres"] = data["genres"].apply(get_names)

In [ ]:
# Reciclo la funcion de arriba para hacer lo mismo con los valores de la columna keywords.

data["keywords"] = data["keywords"].apply(get_names)

In [14]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  In the 22nd century, a paraplegic Marine is di...   
1  Captain Barbossa, long believed to be dead, ha...   
2  A cryptic message from Bond’s past sends him o...   
3  Following the death of District Attorney Harve...   
4  John Carter is a war-weary, former military ca...   

                                          genres  \
0  [Action, Adventure, Fantasy, Science Fiction]   
1                   [Adventure, Fantasy, Action]   
2                     [Action, Adventure, Crime]   
3               [Action, Crime, Drama, Thriller]   
4           [Action, Adventure, Science Fiction]   

                                            keywords  \
0  [culture clash, future, space war, space colon...   
1  [ocean, drug abuse, exotic island, east india ...   
2  [spy, based on novel, secret agent, sequel, mi...   
3  [dc comics, crime fighter, terrorist, secret i...   
4  [based on novel, mars, medallion, space travel...   

                                                cast  \
0  [{'cast_id': 242, 'character': 'Jake Sully', '...   
1  [{'cast_id': 4, 'character': 'Captain Jack Spa...   
2  [{'cast_id': 1, 'character': 'James Bond', 'cr...   
3  [{'cast_id': 2, 'character': 'Bruce Wayne / Ba...   
4  [{'cast_id': 5, 'character': 'John Carter', 'c...   

                                                crew  
0  [{'credit_id': '52fe48009251416c750aca23', 'de...  
1  [{'credit_id': '52fe4232c3a36847f800b579', 'de...  
2  [{'credit_id': '54805967c3a36829b5002c41', 'de...  
3  [{'credit_id': '52fe4781c3a36847f81398c3', 'de...  
4  [{'credit_id': '52fe479ac3a36847f813eaa3', 'de...

In [ ]:
# Para la columna cast aplicamos la misma logica que en las dos columnas anteriores, pero limitamos en tres nombres. (solo queremos obtener los tres primeros nombres)

def get_names_cast(x):

    list_name = []  # Creamos una lista vacía para almacenar los nombres
    contador = 0

    for i in x:  # Iteramos sobre cada elemento en la lista x
        if "name" in i:  # Verificamos que el diccionario tiene la clave "name"
            list_name.append(i["name"])
            contador += 1  # Añadimos el nombre a la lista
            if contador == 3:
                return list_name  # Retornamos la lista con los nombres
            
data["cast"] = data["cast"].apply(get_names_cast)

In [16]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  In the 22nd century, a paraplegic Marine is di...   
1  Captain Barbossa, long believed to be dead, ha...   
2  A cryptic message from Bond’s past sends him o...   
3  Following the death of District Attorney Harve...   
4  John Carter is a war-weary, former military ca...   

                                          genres  \
0  [Action, Adventure, Fantasy, Science Fiction]   
1                   [Adventure, Fantasy, Action]   
2                     [Action, Adventure, Crime]   
3               [Action, Crime, Drama, Thriller]   
4           [Action, Adventure, Science Fiction]   

                                            keywords  \
0  [culture clash, future, space war, space colon...   
1  [ocean, drug abuse, exotic island, east india ...   
2  [spy, based on novel, secret agent, sequel, mi...   
3  [dc comics, crime fighter, terrorist, secret i...   
4  [based on novel, mars, medallion, space travel...   

                                               cast  \
0  [Sam Worthington, Zoe Saldana, Sigourney Weaver]   
1     [Johnny Depp, Orlando Bloom, Keira Knightley]   
2      [Daniel Craig, Christoph Waltz, Léa Seydoux]   
3      [Christian Bale, Michael Caine, Gary Oldman]   
4    [Taylor Kitsch, Lynn Collins, Samantha Morton]   

                                                crew  
0  [{'credit_id': '52fe48009251416c750aca23', 'de...  
1  [{'credit_id': '52fe4232c3a36847f800b579', 'de...  
2  [{'credit_id': '54805967c3a36829b5002c41', 'de...  
3  [{'credit_id': '52fe4781c3a36847f81398c3', 'de...  
4  [{'credit_id': '52fe479ac3a36847f813eaa3', 'de...

In [ ]:
# PAra la columna crew aplicamos esta funcion que solo se queda con el nombre del director, lo podemos encontrar dentro de un subdiccionario que se llama directing

def get_names_crew(x):

    list_name = []  # Creamos una lista vacía para almacenar los nombres

    for i in x:  # Iteramos sobre cada elemento en la lista x
        if i["department"] == 'Directing':  # Verificamos que el diccionario tiene la clave "name"
            list_name.append(i["name"])
            
    return list_name  # Retornamos la lista con los nombres

data["crew"] = data["crew"].apply(get_names_crew)

In [18]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  In the 22nd century, a paraplegic Marine is di...   
1  Captain Barbossa, long believed to be dead, ha...   
2  A cryptic message from Bond’s past sends him o...   
3  Following the death of District Attorney Harve...   
4  John Carter is a war-weary, former military ca...   

                                          genres  \
0  [Action, Adventure, Fantasy, Science Fiction]   
1                   [Adventure, Fantasy, Action]   
2                     [Action, Adventure, Crime]   
3               [Action, Crime, Drama, Thriller]   
4           [Action, Adventure, Science Fiction]   

                                            keywords  \
0  [culture clash, future, space war, space colon...   
1  [ocean, drug abuse, exotic island, east india ...   
2  [spy, based on novel, secret agent, sequel, mi...   
3  [dc comics, crime fighter, terrorist, secret i...   
4  [based on novel, mars, medallion, space travel...   

                                               cast  \
0  [Sam Worthington, Zoe Saldana, Sigourney Weaver]   
1     [Johnny Depp, Orlando Bloom, Keira Knightley]   
2      [Daniel Craig, Christoph Waltz, Léa Seydoux]   
3      [Christian Bale, Michael Caine, Gary Oldman]   
4    [Taylor Kitsch, Lynn Collins, Samantha Morton]   

                                                crew  
0                                    [James Cameron]  
1  [Gore Verbinski, Pamela Alch, Sharron Reynolds...  
2  [Sam Mendes, Jayne-Ann Tenggren, Nicoletta Man...  
3  [Christopher Nolan, Steve Gehrke, Matthew Reed...  
4  [Andrew Stanton, Annie Penn, Tommy Gormley, Be...

In [ ]:
# parqa la columna overview aplicamos una funcion que la convierte en una lista. 

def text_to_list(x):
    # Convertir el texto en una lista que contiene el texto completo como un solo elemento
    return [x]  # Devuelve el texto dentro de una lista

# Aplicamos la función a la columna 'overview' del dataframe
data["overview"] = data["overview"].apply(text_to_list)

In [20]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  [In the 22nd century, a paraplegic Marine is d...   
1  [Captain Barbossa, long believed to be dead, h...   
2  [A cryptic message from Bond’s past sends him ...   
3  [Following the death of District Attorney Harv...   
4  [John Carter is a war-weary, former military c...   

                                          genres  \
0  [Action, Adventure, Fantasy, Science Fiction]   
1                   [Adventure, Fantasy, Action]   
2                     [Action, Adventure, Crime]   
3               [Action, Crime, Drama, Thriller]   
4           [Action, Adventure, Science Fiction]   

                                            keywords  \
0  [culture clash, future, space war, space colon...   
1  [ocean, drug abuse, exotic island, east india ...   
2  [spy, based on novel, secret agent, sequel, mi...   
3  [dc comics, crime fighter, terrorist, secret i...   
4  [based on novel, mars, medallion, space travel...   

                                               cast  \
0  [Sam Worthington, Zoe Saldana, Sigourney Weaver]   
1     [Johnny Depp, Orlando Bloom, Keira Knightley]   
2      [Daniel Craig, Christoph Waltz, Léa Seydoux]   
3      [Christian Bale, Michael Caine, Gary Oldman]   
4    [Taylor Kitsch, Lynn Collins, Samantha Morton]   

                                                crew  
0                                    [James Cameron]  
1  [Gore Verbinski, Pamela Alch, Sharron Reynolds...  
2  [Sam Mendes, Jayne-Ann Tenggren, Nicoletta Man...  
3  [Christopher Nolan, Steve Gehrke, Matthew Reed...  
4  [Andrew Stanton, Annie Penn, Tommy Gormley, Be...

#### Eliminar espacios

In [ ]:
# Función para eliminar los espacios entre palabras en cada elemento de la lista.
def remove_spaces(x):
    if x is None:  # Si la celda es None, devolvemos una lista vacía o la misma celda
        return []
    
    result = []
   
    for i in x:
        result.append(i.replace(" ", ""))
    return result


data["genres"] = data["genres"].apply(remove_spaces)
data["cast"] = data["cast"].apply(remove_spaces)
data["crew"] = data["crew"].apply(remove_spaces)
data["keywords"] = data["keywords"].apply(remove_spaces)

In [22]:
data.head()

movie_id                                   title:1  \
0     19995                                    Avatar   
1       285  Pirates of the Caribbean: At World's End   
2    206647                                   Spectre   
3     49026                     The Dark Knight Rises   
4     49529                               John Carter   

                                            overview  \
0  [In the 22nd century, a paraplegic Marine is d...   
1  [Captain Barbossa, long believed to be dead, h...   
2  [A cryptic message from Bond’s past sends him ...   
3  [Following the death of District Attorney Harv...   
4  [John Carter is a war-weary, former military c...   

                                         genres  \
0  [Action, Adventure, Fantasy, ScienceFiction]   
1                  [Adventure, Fantasy, Action]   
2                    [Action, Adventure, Crime]   
3              [Action, Crime, Drama, Thriller]   
4           [Action, Adventure, ScienceFiction]   

                                            keywords  \
0  [cultureclash, future, spacewar, spacecolony, ...   
1  [ocean, drugabuse, exoticisland, eastindiatrad...   
2  [spy, basedonnovel, secretagent, sequel, mi6, ...   
3  [dccomics, crimefighter, terrorist, secretiden...   
4  [basedonnovel, mars, medallion, spacetravel, p...   

                                            cast  \
0  [SamWorthington, ZoeSaldana, SigourneyWeaver]   
1     [JohnnyDepp, OrlandoBloom, KeiraKnightley]   
2      [DanielCraig, ChristophWaltz, LéaSeydoux]   
3      [ChristianBale, MichaelCaine, GaryOldman]   
4    [TaylorKitsch, LynnCollins, SamanthaMorton]   

                                                crew  
0                                     [JamesCameron]  
1  [GoreVerbinski, PamelaAlch, SharronReynolds, K...  
2  [SamMendes, Jayne-AnnTenggren, NicolettaMani, ...  
3  [ChristopherNolan, SteveGehrke, MatthewReedy, ...  
4  [AndrewStanton, AnniePenn, TommyGormley, BenDi...

In [ ]:
# Reduciremos nuestro conjunto de datos combinando todas nuestras columnas convertidas anteriores en una sola columna llamada `tags` (que crearemos). Esta columna ahora tendrá todos los elementos separados por comas y luego las reemplazaremos por espacios en blanco

# Función para combinar las listas de las columnas 'overview', 'genres', 'keywords', 'cast' y 'crew'

def combine_columns(row):
    # Concatenamos las listas de las columnas
    combined = row['overview'] + row['genres'] + row['keywords'] + row['cast'] + row['crew']
    
    # Aseguramos que cada elemento es una cadena y reemplazamos 'None' por cadena vacía
    combined = [str(i) if i is not None else '' for i in combined]
    
    # Convertimos la lista combinada a una cadena separada por comas
    combined_str = " ".join(combined)  # Unimos los elementos con espacios
    return combined_str

# Aplicamos la función a cada fila
data['tags'] = data.apply(combine_columns, axis=1)

# Verificamos el resultado
print(data[['tags']].head())

                                                tags
0  In the 22nd century, a paraplegic Marine is di...
1  Captain Barbossa, long believed to be dead, ha...
2  A cryptic message from Bond’s past sends him o...
3  Following the death of District Attorney Harve...
4  John Carter is a war-weary, former military ca...


In [ ]:
# Creo mi nuevo dataframe con las columnas que me interesa. 

new_data = data[['title:1', 'tags']]

new_data.head()

title:1  \
0                                    Avatar   
1  Pirates of the Caribbean: At World's End   
2                                   Spectre   
3                     The Dark Knight Rises   
4                               John Carter   

                                                tags  
0  In the 22nd century, a paraplegic Marine is di...  
1  Captain Barbossa, long believed to be dead, ha...  
2  A cryptic message from Bond’s past sends him o...  
3  Following the death of District Attorney Harve...  
4  John Carter is a war-weary, former military ca...

#### Paso 4: Construye un KNN

### Dividir el conjunto de datos en train y test: X_train, X_test

In [80]:
# Dividimos el conjunto de datos en muestras de train y test

X = new_data['tags']

# X_train, X_test = train_test_split(X, test_size = 0.2, random_state = 42)

# X_train.head()

### PROCESAMIENTO DEL TEXTO

#### TfidfVectorizer

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Inicializo el vectorizador.
vec_model = TfidfVectorizer(stop_words = "english")

# Guardo el vectorizador. 
with open("/Users/julian/Desktop/vs code/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/data/Vectorizadores/CountVectorizer.pkl", "wb") as file: 
  pickle.dump(vec_model, file)

# Aplico el TfidfVectorizer 
X_transformed = vec_model.fit_transform(X)



### MACHINE LEARNING

In [47]:
# Librerias necesarias para modelo de regresión logística
import pandas as pd
import numpy as np

#### KNN MODEL

In [ ]:
from sklearn.neighbors import NearestNeighbors

X = X_transformed


model = NearestNeighbors(n_neighbors = 6, metric='cosine').fit(X)
distances, indices = model.kneighbors(X)
indices

import pickle

# Guardo el modelo.
with open("/Users/julian/Desktop/vs code/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/K-NEAREST_NEIGHBORS_model_for_machine_learning_Project_20_Julian_Lopez/models/K-NEAREST_NEIGHBORS_model.sav", "wb") as file:
    pickle.dump(model, file)


#### Función que implementa el modelo para recomendar peliculas.  

In [108]:
import pandas as pd
from sklearn.neighbors import NearestNeighbors

def recomendar_peliculas(pelicula, df, model_knn, X):

    # Verificar que la película esté en el DataFrame
    if pelicula not in df['title:1'].values:
        return "Película no encontrada en el DataFrame."
    
    # Obtener el índice de la película seleccionada
    pelicula_index = df[df['title:1'] == pelicula].index[0]
    
    # Obtener las características de la película seleccionada
    pelicula_data = X[pelicula_index].reshape(1, -1) 
    
    # Encontrar las películas más cercanas usando el modelo KNN
    distancias, indices = model_knn.kneighbors(pelicula_data)
    
    # Obtener los títulos de las 5 películas más cercanas (excluyendo la película misma)
    peliculas_recomendadas = []
    for i in range(1, len(indices[0])):  # Comenzamos en 1 para evitar la misma película
        pelicula_recomendada = df.iloc[indices[0][i]]['title:1']
        peliculas_recomendadas.append(pelicula_recomendada)
    
    return peliculas_recomendadas


pelicula_elegida = 'Avatar'  
recomendacion = recomendar_peliculas(pelicula_elegida, new_data, model, X)

print(f"Si ves la película '{pelicula_elegida}', te recomendamos ver las siguientes películas:")
for pelicula in recomendacion:
    print(pelicula)


Si ves la película 'Avatar', te recomendamos ver las siguientes películas:
Aliens
Battle: Los Angeles
Falcon Rising
Star Trek Into Darkness
Apollo 18
